# Exploração de Dados (EDA)

Este notebook cobre o ponto 3 do trabalho: análises descritivas, gráficos interativos e uma visão geoespacial do dataset pré-processado.

## Etapas abordadas

1. Estatísticas básicas e distribuição da variável alvo.
2. Identificação de outliers via boxplot interativo.
3. Matriz de correlação.
4. Mapas do comportamento geográfico dos pedidos.

### Bibliotecas e visualização

Importamos pandas para manipulação, Plotly para gráficos interativos e `Path` para localizar o CSV pré-processado.

In [1]:
import pandas as pd
import plotly.express as px
import plotly.figure_factory as ff
from pathlib import Path

### Fonte dos dados limpos

Aponta para o CSV produzido pelo pipeline de pré-processamento e garante consistência de caminhos relativos no notebook.

In [10]:
DATA_FILE = Path('/home/arthur/projects/data-eda-proj/data/clean/olist_ml_ready.csv')

### Carregando o dataset preparado

Leitura completa de `data/clean/olist_ml_ready.csv` para que todas as análises descritas usem os registros consolidados.

In [11]:
df = pd.read_csv(DATA_FILE)

In [12]:
print('Linhas:', len(df))
print('Colunas numéricas:', len(df.select_dtypes(include='number').columns))
df[['delivery_time_days', 'distance_km']].describe()


Linhas: 40000
Colunas numéricas: 145


delivery_time_days   distance_km
count        40000.000000  4.000000e+04
mean            12.537025 -1.918465e-17
std              9.502742  1.000013e+00
min              0.781366 -1.033169e+00
25%              6.738979 -7.133434e-01
50%             10.207708 -2.757898e-01
75%             15.690593  3.606753e-01
max            194.049583  1.402996e+01

### Conferência de dimensões e tipos

O bloco abaixo confirma a quantidade de registros lidos e quantas colunas numéricas existem, validando que estamos usando a base completa antes de plotar qualquer gráfico.

### Distribuição da variável alvo

O histograma abaixo evidencia o espalhamento do tempo de entrega (`delivery_time_days`) e ajuda a identificar assimetrias ou múltiplos picos antes de modelar.

In [13]:
fig = px.histogram(
    df,
    x='delivery_time_days',
    nbins=60,
    title='Distribuição interativa do tempo de entrega (dias)',
    color_discrete_sequence=['#636EFA']
)
fig.update_layout(bargap=0.1)
fig.show()


### Detecção de outliers

O boxplot interativo destaca pedidos atípicos, enquanto a tabela mostra exemplos acima do percentil 95% para análise manual.

In [14]:
threshold = df['delivery_time_days'].quantile(0.95)
outliers = df[df['delivery_time_days'] > threshold]
print('Limite 95%:', threshold)
print('Pedidos fora do limite (amostra):')
display(outliers[['order_id', 'delivery_time_days', 'distance_km']].head())
fig_box = px.box(
    df,
    y='delivery_time_days',
    points='all',
    title='Boxplot interativo do tempo de entrega'
)
fig_box.show()


Limite 95%: 29.15095775462951
Pedidos fora do limite (amostra):


order_id  delivery_time_days  distance_km
12  8489131c7dcc42a6d6d7df1be6802643           45.516366     3.487750
17  96192a86ceeb753de81aacdd955288f8           40.671620     1.562007
38  35546dd6349a2065ed8ac6ffbd2b7aba           49.429988     0.683653
51  a7da4c5d1aa10f5bd43694601bea7057           36.385023    -0.287807
55  87a330a52c9e677f1252f2f17e54cf65           32.719560     1.063144

### Matriz de correlação

Explora as relações entre atributos numéricos (tempo de entrega, distância, preços, etc.) e direciona seleções de features ou engenharia futura.

In [15]:
numeric = df.select_dtypes(include='number')
corr = numeric.corr()
fig_corr = ff.create_annotated_heatmap(
    z=corr.values,
    x=list(corr.columns),
    y=list(corr.index),
    annotation_text=corr.round(2).values,
    showscale=True,
    colorscale='Blues'
)
fig_corr.update_layout(height=700, title='Correlação entre variáveis numéricas')
fig_corr.show()


### Distribuição geográfica dos pedidos

Mapa interativo com Mapbox que revela a amplitude espacial dos clientes e permite identificar regiões com maior tempo de entrega.

In [17]:
fig_map = px.scatter_mapbox(
    df,
    lat='customer_latitude',
    lon='customer_longitude',
    hover_name='order_id',
    hover_data=['distance_km', 'delivery_time_days'],
    color='delivery_time_days',
    color_continuous_scale='Turbo',
    zoom=3,
    height=600,
    title='Pontos de entrega dos clientes (toda base)'
)
fig_map.update_layout(mapbox_style='open-street-map')
fig_map.update_traces(marker=dict(opacity=0.6, size=4))
fig_map.show()


/tmp/ipykernel_54889/3554874427.py:2: DeprecationWarning:

*scatter_mapbox* is deprecated! Use *scatter_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

